In [2]:
from sklearn.model_selection import train_test_split
from sklearn.metrics import roc_curve, auc, accuracy_score, recall_score, accuracy_score, recall_score, f1_score, precision_score, roc_auc_score 
import matplotlib.pyplot as plt
from sklearn.neural_network import MLPClassifier
from sklearn.decomposition import PCA
#import matplotlib.patches as mpatches
import numpy as np
import scipy.io as sp
import pandas as pd
#from sklearn.decomposition import PCA
import xlsxwriter
from IPython.display import display
from sklearn.model_selection import StratifiedKFold

#Traitement du fichier .mat
cancercell = sp.loadmat('breastw.mat')
X = cancercell['X']
y = cancercell['y']
#print(cancercell)
y=np.reshape(y,(683,))


In [2]:
#Choix hyperparamètres 

HLS=[]
for j in range(4,8):
    for k in range(4,7):
        HLS.append((j,k))
Alpha = [1, 0.1, 0.01, 0.001]
Solver = ['lbfgs', 'sgd','adam']
Activation = ['identity', 'logistic', 'tanh', 'relu']
Max_iter = []
for k in range(4,7):
    Max_iter.append(2*k)

   
skf = StratifiedKFold(n_splits=10,shuffle=True) # équilibrage dataset

In [3]:
skf = StratifiedKFold(n_splits=10,shuffle=True) # équilibrage dataset

for train_index, test_index in skf.split(X,y):
    
    test =False
    X_train, X_test = X[train_index,:], X[test_index,:]
    y_train, y_test = y[train_index], y[test_index]
    y_train=np.ravel(y_train)
    y_test=np.ravel(y_test)

    #Méthode MLP

    test =False
    for k in HLS :
        for i in Alpha :
            for j in Solver :
                for p in Activation : 
                    model_MLP = MLPClassifier(hidden_layer_sizes = k, alpha = i, solver = j, activation = p , max_iter = 15)
                    model_MLP.fit(X_train,y_train)
                    y_pred_MLP = model_MLP.predict(X_test)
                                            
                    y_scores_MLP = model_MLP.predict_proba(X_test)
                    y_scores_MLP = y_scores_MLP[:, 1]
                                            
                    F1_MLP = round(f1_score(y_test,y_pred_MLP),3)
                        
                    if test == False :
                        data = np.array([[k,i,j,p,F1_MLP]])
                        test = True
                    else :
                        data = np.append(data,np.array([k,i,j,p,F1_MLP]).reshape(1,5),axis=0)
                    #Fin méthode MLP
            

df = pd.DataFrame(data, columns=['Hidden_layers','Alpha','Solver','Activation','F1 score'])
df = df.astype({'F1 score': float})

filtered_values_1 = np.where((df['F1 score']>=0.96))
display(df.iloc[filtered_values_1].sort_values(by=['F1 score'], ascending=False))



/Library/Frameworks/Python.framework/Versions/3.10/lib/python3.10/site-packages/sklearn/neural_network/_multilayer_perceptron.py:549: ConvergenceWarning: lbfgs failed to converge (status=1):
STOP: TOTAL NO. of ITERATIONS REACHED LIMIT.

Increase the number of iterations (max_iter) or scale the data as shown in:
    https://scikit-learn.org/stable/modules/preprocessing.html
  self.n_iter_ = _check_optimize_result("lbfgs", opt_res, self.max_iter)
/var/folders/s6/p3txrvvd4498vs_xw7ryvx7h0000gn/T/ipykernel_4852/4045784616.py:28: VisibleDeprecationWarning: Creating an ndarray from ragged nested sequences (which is a list-or-tuple of lists-or-tuples-or ndarrays with different lengths or shapes) is deprecated. If you meant to do this, you must specify 'dtype=object' when creating the ndarray.
  data = np.array([[k,i,j,p,F1_MLP]])
/Library/Frameworks/Python.framework/Versions/3.10/lib/python3.10/site-packages/sklearn/neural_network/_multilayer_perceptron.py:549: ConvergenceWarning: lbfgs faile

Hidden_layers  Alpha Solver Activation  F1 score
15         (4, 4)    0.1  lbfgs       relu     1.000
87         (4, 5)  0.001  lbfgs       relu     1.000
288        (6, 4)      1  lbfgs   identity     1.000
255        (5, 6)    0.1  lbfgs       relu     0.980
547        (7, 6)    0.1    sgd       relu     0.980
555        (7, 6)   0.01  lbfgs       relu     0.980
72         (4, 5)   0.01  lbfgs   identity     0.979
219        (5, 5)   0.01  lbfgs       relu     0.979
267        (5, 6)   0.01  lbfgs       relu     0.979
336        (6, 5)      1  lbfgs   identity     0.979
399        (6, 6)    0.1  lbfgs       relu     0.979
471        (7, 4)  0.001  lbfgs       relu     0.979
567        (7, 6)  0.001  lbfgs       relu     0.979
271        (5, 6)   0.01    sgd       relu     0.960

In [4]:


filtered_values_2 = np.where((df['F1 score']>=0.98))
display(df.iloc[filtered_values_2].sort_values(by=['F1 score'], ascending=False))

Hidden_layers  Alpha Solver Activation  F1 score
15         (4, 4)    0.1  lbfgs       relu      1.00
87         (4, 5)  0.001  lbfgs       relu      1.00
288        (6, 4)      1  lbfgs   identity      1.00
255        (5, 6)    0.1  lbfgs       relu      0.98
547        (7, 6)    0.1    sgd       relu      0.98
555        (7, 6)   0.01  lbfgs       relu      0.98

In [4]:
# evaluate label propagation on the semi-supervised learning dataset
from scipy.stats import f_oneway

dataSet = sp.loadmat('breastw.mat')
X = dataSet['X']
y = dataSet['y']
Combinaisons = [[(4,4), 0.1, 'lbfgs','relu'], [(4,5), 0.001, 'lbfgs','relu'], [(6,5), 1, 'lbfgs','identity'], [(5,6), 0.1, 'lbfgs','relu'], [(7,6), 0.1, 'sgd','relu'], [(7,6), 0.01, 'lbfgs','relu']]
skf2 = StratifiedKFold(n_splits=10) 
fold=0

algo = 0
for C in Combinaisons:
        test=False
        for train_index, test_index in skf2.split(X, y):
                fold=fold+1
                
                X_train, X_test = X[train_index,:], X[test_index,:]
                y_train, y_test = y[train_index], y[test_index]
                        
                model_MLP = MLPClassifier(hidden_layer_sizes=C[0], alpha=C[1], solver=C[2], activation=C[3])
                model_MLP.fit(X_train,y_train)
                y_pred_MLP = model_MLP.predict(X_test)
                        
                F1=round(f1_score(y_test,y_pred_MLP),3)
                    
                liste = '_'.join([str(elem) for elem in C ])
                if test==False :
                        data = np.array([[F1]])
                        test=True
                else :
                        data = np.append(data,np.array([F1]).reshape(1,1),axis=0)
        if algo == 0  :
                df2=pd.DataFrame(data,columns=['[{}]'.format(liste)])
                        
        else :
                df=pd.DataFrame(data,columns=['[{}]'.format(liste)])
                df2=pd.concat([df2, df], axis = 1)
        algo = algo + 1
        
display(df2)
 

/Library/Frameworks/Python.framework/Versions/3.10/lib/python3.10/site-packages/sklearn/neural_network/_multilayer_perceptron.py:1109: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples, ), for example using ravel().
  y = column_or_1d(y, warn=True)
/Library/Frameworks/Python.framework/Versions/3.10/lib/python3.10/site-packages/sklearn/neural_network/_multilayer_perceptron.py:1109: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples, ), for example using ravel().
  y = column_or_1d(y, warn=True)
/Library/Frameworks/Python.framework/Versions/3.10/lib/python3.10/site-packages/sklearn/neural_network/_multilayer_perceptron.py:1109: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples, ), for example using ravel().
  y = column_or_1d(y, warn=True)
/Library/Frameworks/Python.f

[(4, 4)_0.1_lbfgs_relu]  [(4, 5)_0.001_lbfgs_relu]  \
0                    0.800                      0.773   
1                    0.769                      0.696   
2                    0.898                      0.941   
3                    0.917                      0.936   
4                    1.000                      0.980   
5                    0.939                      0.958   
6                    0.958                      0.958   
7                    1.000                      1.000   
8                    0.958                      0.979   
9                    1.000                      0.980   

   [(6, 5)_1_lbfgs_identity]  [(5, 6)_0.1_lbfgs_relu]  [(7, 6)_0.1_sgd_relu]  \
0                      0.894                    0.917                  0.851   
1                      0.957                    0.913                  0.737   
2                      0.920                    0.898                  0.941   
3                      0.917                    0.917                  0.936   
4                      1.000                    0.980                  0.980   
5                      0.958                    0.958                  0.880   
6                      0.936                    0.957                  0.980   
7                      1.000                    0.980                  1.000   
8                      0.957                    0.958                  0.870   
9                      1.000                    0.980                  0.980   

   [(7, 6)_0.01_lbfgs_relu]  
0                     0.800  
1                     0.933  
2                     0.920  
3                     0.917  
4                     0.960  
5                     0.920  
6                     0.958  
7                     0.980  
8                     1.000  
9                     0.957

In [5]:
t,p = f_oneway(df2['[(4, 4)_0.1_lbfgs_relu]'],df2['[(4, 5)_0.001_lbfgs_relu]'],df2['[(6, 5)_1_lbfgs_identity]'],df2['[(5, 6)_0.1_lbfgs_relu]'],df2['[(7, 6)_0.1_sgd_relu]'],df2['[(7, 6)_0.01_lbfgs_relu]'])
print('t statistic: %.3f' % t)
print('p value: %.13f' % p)

t statistic: 0.478
p value: 0.7912512586984
